In [1]:
from inicio_programa import train_pam_biped

train_pam_biped(total_timesteps=1000000, n_envs=1, learning_rate=1e-4,
                resume=False, action_space="hybrid")

🚀 Starting PAM biped training...
🤖 Starting PAM biped training with RecurrentPPO (LSTM)...
🎯 Training plan:
   - Completed: 0 timesteps
   - Remaining: 1,000,000 timesteps
   - Total target: 1,000,000 timesteps
📊 PAM Training Features:
   - Hybrid IK + PAM control
   - Realistic tensile forces
   - LSTM memory for muscle coordination
   - Energy efficiency optimization
📦 Creating 1 training environments...
Observation space: (34,)
   ✅ Walking cycle enabled for training env
Observation space: (34,)
   ✅ Walking cycle enabled for training env
🧠 Creating RecurrentPPO model with LSTM architecture...
🧠 Creating new RecurrentPPO model...
Using cuda device
📊 Training Plan:
   - Phase 1: 300,000 steps (Walking cycle base)
   - Phase 2: 400,000 steps (Cycle + RL modulation)
   - Phase 3: 300,000 steps (Full RL control)
📊 Model Configuration:
   - Algorithm: RecurrentPPO
   - Policy: MlpLstmPolicy
   - Environment: PAM
   - Architecture: {'pi': [256, 256, 128], 'vf': [256, 256, 128]}
   - Learn

error: Not connected to physics server.

In [ ]:
from inicio_programa import test_pam_biped

test_pam_biped(model_path="models/best_model.zip", action_space="hybrid")

Testing PAM RecurrentPPO model: models/best_model.zip
Observation space: (34,)
Loading normalization statistics...
marcha atrás (-0.34576495931323115, -0.9791342187887409, -1.5777433259372633)
Episode 1: Reward = -1411.80, Steps = 1034
marcha atrás (-0.34576495931323115, -0.9791342187887409, -1.5777433259372633)
Episode 2: Reward = -1411.80, Steps = 1034
marcha atrás (-0.34576495931323115, -0.9791342187887409, -1.5777433259372633)
Episode 3: Reward = -1411.80, Steps = 1034
marcha atrás (-0.34576495931323115, -0.9791342187887409, -1.5777433259372633)
Episode 4: Reward = -1411.80, Steps = 1034
marcha atrás (-0.34576495931323115, -0.9791342187887409, -1.5777433259372633)
Episode 5: Reward = -1411.80, Steps = 1034
marcha atrás (-0.34576495931323115, -0.9791342187887409, -1.5777433259372633)
Episode 6: Reward = -1411.80, Steps = 1034
marcha atrás (-0.34576495931323115, -0.9791342187887409, -1.5777433259372633)
Episode 7: Reward = -1411.80, Steps = 1034


In [1]:
import numpy as np
import pickle
from bided_pam_IK import PAMIKBipedEnv
from Archivos_Apoyo.SimplifiedWalkingController import SimplifiedWalkingController

env = PAMIKBipedEnv(render_mode='direct', action_space='hybrid')
controller = SimplifiedWalkingController(env)
dataset = []

obs, info = env.reset()
controller.reset()

for step in range(200000):  # O el número de pasos que quieras grabar
    expert_action = controller.get_next_action()
    dataset.append((obs.copy(), expert_action.copy()))
    obs, reward, done, truncated, info = env.step(expert_action)
    if done:
        obs, info = env.reset()
        controller.reset()
        # Puedes grabar solo pasos iniciales por episodio si quieres

# Guardar el dataset
with open('expert_dataset.pkl', 'wb') as f:
    pickle.dump(dataset, f)

Observation space: (34,)
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIMPLE
PAM_SIM

In [2]:
import torch
import torch.nn as nn
import torch.optim as optim
import pickle

# Carga tu dataset experto
with open('expert_dataset.pkl', 'rb') as f:
    dataset = pickle.load(f)
X = np.array([d[0] for d in dataset], dtype=np.float32)  # observaciones
Y = np.array([d[1] for d in dataset], dtype=np.float32)  # acciones

# Red neuronal simple (ajusta a tu observación/acción space)
class PolicyNet(nn.Module):
    def __init__(self, obs_dim, act_dim):
        super().__init__()
        self.fc = nn.Sequential(
            nn.Linear(obs_dim, 128),
            nn.ReLU(),
            nn.Linear(128, 128),
            nn.ReLU(),
            nn.Linear(128, act_dim),
            nn.Tanh(),  # Si tus acciones están en [-1, 1]
        )
    def forward(self, x):
        return self.fc(x)

obs_dim = X.shape[1]
act_dim = Y.shape[1]
policy = PolicyNet(obs_dim, act_dim)
optimizer = optim.Adam(policy.parameters(), lr=1e-3)
loss_fn = nn.MSELoss()

# Entrenamiento supervisado
for epoch in range(100):  # Ajusta epochs
    idx = np.random.permutation(len(X))
    X_shuf, Y_shuf = X[idx], Y[idx]
    for i in range(0, len(X), 256):
        x_batch = torch.from_numpy(X_shuf[i:i+256])
        y_batch = torch.from_numpy(Y_shuf[i:i+256])
        pred = policy(x_batch)
        loss = loss_fn(pred, y_batch)
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()
    print(f"Epoch {epoch}: Loss={loss.item()}")

# Puedes guardar la policy entrenada:
torch.save(policy.state_dict(), "bc_policy.pth")

Epoch 0: Loss=0.0003986444789916277
Epoch 1: Loss=0.000209177378565073
Epoch 2: Loss=9.686986595625058e-05
Epoch 3: Loss=7.284005550900474e-05
Epoch 4: Loss=0.00013049425615463406
Epoch 5: Loss=7.514984463341534e-05
Epoch 6: Loss=6.457674317061901e-05
Epoch 7: Loss=2.7411539122113027e-05
Epoch 8: Loss=5.059238173998892e-05
Epoch 9: Loss=2.225046955572907e-05
Epoch 10: Loss=2.1876949176657945e-05
Epoch 11: Loss=1.363013234367827e-05
Epoch 12: Loss=1.566962782817427e-05
Epoch 13: Loss=4.243542207404971e-05
Epoch 14: Loss=1.8184155123890378e-05
Epoch 15: Loss=1.6110658179968596e-05
Epoch 16: Loss=1.5390640328405425e-05
Epoch 17: Loss=2.1698911950807087e-05
Epoch 18: Loss=1.8821277990355156e-05
Epoch 19: Loss=1.154336041508941e-05
Epoch 20: Loss=3.642475712695159e-05
Epoch 21: Loss=4.074582193425158e-06
Epoch 22: Loss=9.732217222335748e-06
Epoch 23: Loss=1.0667885362636298e-05
Epoch 24: Loss=1.2205998245917726e-05
Epoch 25: Loss=9.109524398809299e-06
Epoch 26: Loss=8.257296940428205e-06
Ep